In [ ]:
import pandas as pd
import torch
from transformers import BertTokenizer
from transformers import BertForSequenceClassification
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from keras.preprocessing.sequence import pad_sequences
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
from torch.optim import AdamW
from transformers import get_linear_schedule_with_warmup

In [ ]:
df = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/CodigoChatVF/datosChat.csv')
df.head(5)

pregunta pregunta_limpia  \
0                        Hola            hola   
1          Hola, ¿cómo te va?         hola ir   
2                    Buen día        buen dia   
3  ¡Hola! ¿Qué tal estás hoy?    hola tal hoy   
4              Hola ¡Saludos!    hola saludos   

                                         respuesta    label  
0                   ¡Hola! ¿En qué puedo ayudarte?  saludos  
1  ¡Hola! Estoy aquí para responder tus preguntas.  saludos  
2               ¡Buen día! ¿En qué puedo ayudarte?  saludos  
3     Estoy bien, gracias. ¿En qué puedo ayudarte?  saludos  
4               ¡Saludos! ¿Qué puedo hacer por ti?  saludos

In [ ]:
# Creamos un objeto LabelEncoder
label_encoder = LabelEncoder()
# Convertimos las etiquetas de texto a números enteros
df['label_codigo'] = label_encoder.fit_transform(df['label'])
# Obtenemos la correspondencia entre números y etiquetas
label_dict = {i: label for i, label in enumerate(label_encoder.classes_)}
#print(label_dict)

In [ ]:
df.tail(5)

pregunta  \
925  ¿Qué podemos encontrar en la superficie de Plu...   
926          ¿Hay montañas en la superficie de Plutón?   
927                     ¿Cómo es el terreno de Plutón?   
928              ¿Qué tipo de superficie tiene Plutón?   
929  ¿Qué descubrimientos se han hecho sobre la sup...   

                                 pregunta_limpia  \
925             poder encontrar superficie pluto   
926               haber montaña superficie pluto   
927                            ser terreno pluto   
928                  tipo superficie tener pluto   
929  descubrimiento haber hacer superficie pluto   

                                             respuesta              label  \
925  Se sabe que la superficie de Plutón es muy var...  pluton_superficie   
926  Sí, se han encontrado montañas en la superfici...  pluton_superficie   
927  El terreno de Plutón es muy variado e incluye ...  pluton_superficie   
928  La superficie de Plutón está compuesta princip...  pluton_superficie   
929  Algunos de los descubrimientos más interesante...  pluton_superficie   

     label_codigo  
925            50  
926            50  
927            50  
928            50  
929            50

In [ ]:
data_texto  = df["pregunta_limpia"].to_list()  # Features (aun no estan tokenizado)
data_labels = df["label_codigo"].to_list() # Labels

## **Division del conjunto de train, validation y test**

In [ ]:
train_text, temp_text, train_labels, temp_labels = train_test_split(data_texto, data_labels, random_state=2023, test_size=0.3, stratify=df['label_codigo'])
val_text, test_text, val_labels, test_labels = train_test_split(temp_text, temp_labels, random_state=2023, test_size=0.5, stratify=temp_labels)

In [ ]:
tokenizer = BertTokenizer.from_pretrained("dccuchile/bert-base-spanish-wwm-cased", do_lower_case=True)
tokenizer

BertTokenizer(name_or_path='dccuchile/bert-base-spanish-wwm-cased', vocab_size=31002, model_max_length=512, is_fast=False, padding_side='right', truncation_side='right', special_tokens={'unk_token': '[UNK]', 'sep_token': '[SEP]', 'pad_token': '[PAD]', 'cls_token': '[CLS]', 'mask_token': '[MASK]'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
	0: AddedToken("[MASK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	1: AddedToken("[PAD]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	3: AddedToken("[UNK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	4: AddedToken("[CLS]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	5: AddedToken("[SEP]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
}

In [ ]:
def encode(docs):
    '''Esta función toma una lista de textos y devuelve input_ids y atención_mask de textos'''
    encoded_dict = tokenizer.batch_encode_plus(docs, add_special_tokens=True, max_length=128, padding='max_length', #128
                            return_attention_mask=True, truncation=True, return_tensors='pt')
    input_ids = encoded_dict['input_ids']
    attention_masks = encoded_dict['attention_mask']
    return input_ids, attention_masks

In [ ]:
train_input_ids, train_att_masks = encode(train_text)
valid_input_ids, valid_att_masks = encode(val_text)
test_input_ids, test_att_masks   = encode(test_text)

In [ ]:
train_y = torch.LongTensor(train_labels)
valid_y = torch.LongTensor(val_labels)
test_y = torch.LongTensor(test_labels)

In [ ]:
BATCH_SIZE = 32
train_dataset = TensorDataset(train_input_ids, train_att_masks, train_y)
train_sampler = RandomSampler(train_dataset)
train_dataloader = DataLoader(train_dataset, sampler=train_sampler, batch_size=BATCH_SIZE)

valid_dataset = TensorDataset(valid_input_ids, valid_att_masks, valid_y)
valid_sampler = SequentialSampler(valid_dataset)
valid_dataloader = DataLoader(valid_dataset, sampler=valid_sampler, batch_size=BATCH_SIZE)

test_dataset = TensorDataset(test_input_ids, test_att_masks, test_y)
test_sampler = SequentialSampler(test_dataset)
test_dataloader = DataLoader(test_dataset, sampler=test_sampler, batch_size=BATCH_SIZE)

In [ ]:
N_labels = len(df.label.unique())
model = BertForSequenceClassification.from_pretrained("dccuchile/bert-base-spanish-wwm-cased", num_labels=N_labels, output_attentions=False, output_hidden_states=False)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at dccuchile/bert-base-spanish-wwm-cased and are newly initialized: ['bert.pooler.dense.bias', 'classifier.weight', 'classifier.bias', 'bert.pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)

cuda


In [ ]:
model = model.to(device)
model

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(31002, 768, padding_idx=1)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12,

In [ ]:
EPOCHS = 300
LEARNING_RATE = 2e-6

optimizer = AdamW(model.parameters(), lr=LEARNING_RATE)
scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=0,num_training_steps=len(train_dataloader)*EPOCHS )

In [ ]:
from torch.nn.utils import clip_grad_norm_
from tqdm.notebook import tqdm
import numpy as np
import math
import time

train_loss_per_epoch = []
val_loss_per_epoch = []
train_acc_per_epoch = []
val_acc_per_epoch = []
start_time = time.time()

for epoch_num in range(EPOCHS):
    print('Epoch: ', epoch_num + 1)
    '''Training'''
    model.train()
    train_loss = 0
    train_correct = 0
    train_total = 0
    for step_num, batch_data in enumerate(tqdm(train_dataloader,desc='Training')):
        input_ids, att_mask, labels = [data.to(device) for data in batch_data]
        output = model(input_ids = input_ids, attention_mask=att_mask, labels= labels)

        loss = output.loss
        train_loss += loss.item()

        model.zero_grad()
        loss.backward()
        del loss

        clip_grad_norm_(parameters=model.parameters(), max_norm=1.0)
        optimizer.step()
        scheduler.step()

        _, predicted = torch.max(output.logits.data, 1)
        train_total += labels.size(0)
        train_correct += (predicted == labels).sum().item()

    train_loss_per_epoch.append(train_loss / (step_num + 1))
    train_acc_per_epoch.append(train_correct / train_total)

    '''
    Validation
    '''
    model.eval()
    valid_loss = 0
    valid_correct = 0
    valid_total = 0
    valid_pred = []
    with torch.no_grad():
        for step_num_e, batch_data in enumerate(tqdm(valid_dataloader,desc='Validation')):
            input_ids, att_mask, labels = [data.to(device) for data in batch_data]
            output = model(input_ids = input_ids, attention_mask=att_mask, labels= labels)

            loss = output.loss
            valid_loss += loss.item()

            _, predicted = torch.max(output.logits.data, 1)
            valid_total += labels.size(0)
            valid_correct += (predicted == labels).sum().item()
            valid_pred.append(np.argmax(output.logits.cpu().detach().numpy(),axis=-1))

    val_loss_per_epoch.append(valid_loss / (step_num_e + 1))
    val_acc_per_epoch.append(valid_correct / valid_total)
    valid_pred = np.concatenate(valid_pred)

    '''
    Loss message
    '''
    print(f"Train Loss: {train_loss_per_epoch[-1]:.4f}, Train Acc: {train_acc_per_epoch[-1]:.4f}")
    print(f"Val Loss: {val_loss_per_epoch[-1]:.4f}, Val Acc: {val_acc_per_epoch[-1]:.4f}")

    #print("{0}/{1} train loss: {2}, train acc: {3}".format(step_num + 1, math.ceil(len(train_text) / BATCH_SIZE), train_loss / (step_num + 1), train_acc_per_epoch[-1]))
    #print("{0}/{1} val loss: {2}, val acc: {3}".format(step_num_e + 1, math.ceil(len(test_text) / BATCH_SIZE), valid_loss / (step_num_e + 1), val_acc_per_epoch[-1]))

    #print("{0}/{1} train loss: {2} ".format(step_num+1, math.ceil(len(train_text) / BATCH_SIZE), train_loss / (step_num + 1)))
    #print("{0}/{1} val loss: {2} ".format(step_num_e+1, math.ceil(len(test_text) / BATCH_SIZE), valid_loss / (step_num_e + 1)))


end_time = time.time()

# Tiempo de entrenamiento en segundos
training_time = end_time - start_time

print("Tiempo de entrenamiento: {:.2f} segundos".format(training_time))

train_accuracy = (train_correct / train_total) * 100
valid_accuracy = (valid_correct / valid_total) * 100

print("Precisión en el entrenamiento: {:.2f}%".format(train_accuracy))
print("Precisión en la validación: {:.2f}%".format(valid_accuracy))

Epoch:  1


Training:   0%|          | 0/21 [00:00<?, ?it/s]

Validation:   0%|          | 0/5 [00:00<?, ?it/s]

Train Loss: 4.5565, Train Acc: 0.0184
Val Loss: 4.5063, Val Acc: 0.0432
Epoch:  2


Training:   0%|          | 0/21 [00:00<?, ?it/s]

...

Train Loss: 1.0111, Train Acc: 0.9877
Val Loss: 1.1766, Val Acc: 0.8777
Epoch:  155


Training:   0%|          | 0/21 [00:00<?, ?it/s]

Validation:   0%|          | 0/5 [00:00<?, ?it/s]

Train Loss: 1.0005, Train Acc: 0.9892
Val Loss: 1.1706, Val Acc: 0.8777
Epoch:  156


Training:   0%|          | 0/21 [00:00<?, ?it/s]

In [ ]:
from matplotlib import pyplot as plt

epochs = range(1, EPOCHS + 1)

fig, ax = plt.subplots(1, 2, figsize=(15, 5))

ax[0].plot(epochs, train_loss_per_epoch, label='Training Loss')
ax[0].plot(epochs, val_loss_per_epoch, label='Validation Loss')
ax[0].set_title('Training and Validation Loss')
ax[0].set_xlabel('Epochs')
ax[0].set_ylabel('Loss')
ax[0].legend()
ax[0].grid(True, color='black', alpha=0.3)  # Agregar cuadrícula

ax[1].plot(epochs, train_acc_per_epoch, label='Training Accuracy')
ax[1].plot(epochs, val_acc_per_epoch, label='Validation Accuracy')
ax[1].set_title('Training and Validation Accuracy')
ax[1].set_xlabel('Epochs')
ax[1].set_ylabel('Accuracy')
ax[1].legend()
ax[1].grid(True, color='black', alpha=0.3)  # Agregar cuadrícula

plt.show()


In [ ]:
from sklearn.metrics import classification_report

# Convertir valid_y de tensor a un array NumPy
valid_y_numpy = valid_y.cpu().detach().numpy()

# Generar el classification report
print('Classification Report:')
print(classification_report(valid_pred, valid_y_numpy, target_names=label_dict.values(), zero_division=1))


In [ ]:
from sklearn.metrics import precision_score, recall_score, f1_score

# Calculando precision, recall y F-score con zero_division=1
precision = precision_score(valid_y_numpy, valid_pred, average='weighted', zero_division=1)
recall = recall_score(valid_y_numpy, valid_pred, average='weighted', zero_division=1)
f1 = f1_score(valid_y_numpy, valid_pred, average='weighted', zero_division=1)

print('Precision:', precision)
print('Recall:', recall)
print('F1 Score:', f1)

In [ ]:
from sklearn.metrics import confusion_matrix

# Genera la matriz de confusión
cm = confusion_matrix(valid_pred, valid_y_numpy)

# Calcula los porcentajes con manejo de división por cero
cm_sum = cm.sum(axis=1)[:, np.newaxis]
cm_sum[cm_sum == 0] = 1  # Reemplaza los ceros por uno para evitar la división por cero
cm_percentage = cm.astype('float') / cm_sum * 100

# Restaura los ceros en las posiciones originales de la matriz de suma
cm_sum[cm_sum == 1] = 0

# Define las etiquetas de las clases
class_names = [str(i) for i in range(cm.shape[0])]  # Ajustar a la forma correcta de la matriz de confusión

# Ajusta el tamaño de la figura
plt.figure(figsize=(25, 15))   # Cambia las dimensiones según sea necesario

# Crea el plot de la matriz de confusión con porcentajes
plt.imshow(cm_percentage, interpolation='nearest',cmap=plt.cm.Blues)
#plt.colorbar()
plt.xticks(np.arange(len(class_names)), class_names, fontsize=5)  # Ajusta el tamaño de la fuente en el eje x
plt.yticks(np.arange(len(class_names)), class_names, fontsize=5)  # Ajusta el tamaño de la fuente en el eje y
plt.xlabel('Etiqueta Real', fontsize=10)  # Ajusta el tamaño de la fuente para la etiqueta del eje x
plt.ylabel('Etiqueta Predicha', fontsize=10)  # Ajusta el tamaño de la fuente para la etiqueta del eje y
plt.title('Matriz de Confusión ', fontsize=12)  # Ajusta el tamaño de la fuente para el título

# Añade los valores de los porcentajes de la matriz de confusión a cada celda con texto más pequeño
for i in range(cm_percentage.shape[0]):
    for j in range(cm_percentage.shape[1]):
        plt.text(j, i, f'{cm_percentage[i, j]:.0f}',  # Formatea el texto como porcentaje con dos decimales
                ha="center", va="center",
                fontsize=5,  # Ajusta el tamaño de la fuente en las celdas
                color="white" if cm_percentage[i, j] > 50 else "black")  # Cambia el color del texto según un umbral (opcional)

# Muestra el plot
plt.show()

In [ ]:
test_loss = 0
correct_test = 0
total_test = 0
test_pred = []

model.eval()  # Colocar el modelo en modo de evaluación

with torch.no_grad():
    for batch in test_dataloader:
        batch = tuple(t.to(device) for t in batch)
        inputs, masks, labels = batch
        outputs = model(inputs, masks)
        loss = criterion(outputs, labels)
        test_loss += loss.item()
        _, predicted = torch.max(outputs, 1)
        correct_test += (predicted == labels).sum().item()
        total_test += labels.size(0)

        test_pred.append(predicted.cpu().detach().numpy())  # Guardar las predicciones del conjunto de prueba

test_loss = test_loss / len(test_dataloader)
test_accuracy = (correct_test / total_test) * 100
test_pred = np.concatenate(test_pred)

print(f"Test Loss: {test_loss:.4f} - Test Accuracy: {test_accuracy:.2f}%")


In [ ]:
#model.eval()
#test_pred = []
#test_loss= 0
#with torch.no_grad():
#    for step_num, batch_data in tqdm(enumerate(test_dataloader)):
#        input_ids, att_mask, labels = [data.to(device) for data in batch_data]
#        output = model(input_ids = input_ids, attention_mask=att_mask, labels= labels)
#
#        loss = output.loss
#        test_loss += loss.item()
#
#        test_pred.append(np.argmax(output.logits.cpu().detach().numpy(),axis=-1))
#test_pred = np.concatenate(test_pred)

In [ ]:
from sklearn.metrics import classification_report

# Convertir valid_y de tensor a un array NumPy
test_y_numpy = test_y.cpu().detach().numpy()

# Generar el classification report
print('Classification Report:')
print(classification_report(test_pred, test_y_numpy, target_names=label_dict.values(), zero_division=1))


In [ ]:
from sklearn.metrics import precision_score, recall_score, f1_score

# Calculando precision, recall y F-score con zero_division=1
precision = precision_score(test_y_numpy, test_pred, average='weighted', zero_division=1)
recall = recall_score(test_y_numpy, test_pred, average='weighted', zero_division=1)
f1 = f1_score(test_y_numpy, test_pred, average='weighted', zero_division=1)

print('Precision:', precision)
print('Recall:', recall)
print('F1 Score:', f1)

In [ ]:
from sklearn.metrics import confusion_matrix

# Genera la matriz de confusión
cm = confusion_matrix(test_pred, test_y_numpy)

# Calcula los porcentajes con manejo de división por cero
cm_sum = cm.sum(axis=1)[:, np.newaxis]
cm_sum[cm_sum == 0] = 1  # Reemplaza los ceros por uno para evitar la división por cero
cm_percentage = cm.astype('float') / cm_sum * 100

# Restaura los ceros en las posiciones originales de la matriz de suma
cm_sum[cm_sum == 1] = 0

# Define las etiquetas de las clases
class_names = [str(i) for i in range(cm.shape[0])]  # Ajustar a la forma correcta de la matriz de confusión

# Ajusta el tamaño de la figura
plt.figure(figsize=(25, 15))   # Cambia las dimensiones según sea necesario

# Crea el plot de la matriz de confusión con porcentajes
plt.imshow(cm_percentage, interpolation='nearest',cmap=plt.cm.Blues)
#plt.colorbar()
plt.xticks(np.arange(len(class_names)), class_names, fontsize=5)  # Ajusta el tamaño de la fuente en el eje x
plt.yticks(np.arange(len(class_names)), class_names, fontsize=5)  # Ajusta el tamaño de la fuente en el eje y
plt.xlabel('Etiqueta Real', fontsize=10)  # Ajusta el tamaño de la fuente para la etiqueta del eje x
plt.ylabel('Etiqueta Predicha', fontsize=10)  # Ajusta el tamaño de la fuente para la etiqueta del eje y
plt.title('Matriz de Confusión ', fontsize=12)  # Ajusta el tamaño de la fuente para el título

# Añade los valores de los porcentajes de la matriz de confusión a cada celda con texto más pequeño
for i in range(cm_percentage.shape[0]):
    for j in range(cm_percentage.shape[1]):
        plt.text(j, i, f'{cm_percentage[i, j]:.0f}',  # Formatea el texto como porcentaje con dos decimales
                ha="center", va="center",
                fontsize=5,  # Ajusta el tamaño de la fuente en las celdas
                color="white" if cm_percentage[i, j] > 50 else "black")  # Cambia el color del texto según un umbral (opcional)

# Muestra el plot
plt.show()

In [ ]:
test_df = pd.DataFrame({'pred': test_pred, 'label': test_labels})
test_df

In [ ]:
test_df["text"] = test_text

In [ ]:
print(test_df[test_df['label']!=test_df['pred']].shape)
test_df[test_df['label']!=test_df['pred']][['text','label','pred']].head(18)

In [ ]:
# Guardar el modelo después de entrenar
ruta_modelo = 'modelo-clasficacion-preguntas'

# Asegúrate de que el modelo esté en la CPU antes de guardar
model = model.cpu()

# Guardar el modelo y el tokenizer
model.save_pretrained(ruta_modelo)
tokenizer.save_pretrained(ruta_modelo)

In [ ]:
from transformers import BertForSequenceClassification, BertTokenizer

ruta_modelo = '/content/modelo-clasficacion-preguntas'

# Cargar el modelo y el tokenizer
model = BertForSequenceClassification.from_pretrained(ruta_modelo)
tokenizer = BertTokenizer.from_pretrained(ruta_modelo)
tokenizer

In [ ]:
# Texto de ejemplo para hacer una predicción
texto_ejemplo = "como afecta la atmosfera de marte a las misiones espaciales"

# Tokenizar el texto de ejemplo y convertirlo a IDs
inputs = tokenizer(texto_ejemplo, return_tensors="pt")
input_ids = inputs["input_ids"]
attention_mask = inputs["attention_mask"]

# Realizar la predicción
with torch.no_grad():
    outputs = model(input_ids, attention_mask=attention_mask)
    predictions = torch.argmax(outputs.logits, dim=1)

# Obtener la etiqueta predicha usando el label_dict
label_id = predictions.item()
predicted_label = label_dict[label_id]

print("Texto de ejemplo:", texto_ejemplo)
print("Etiqueta predicha:", predicted_label)

In [ ]:
# Texto de ejemplo para hacer una predicción
texto_ejemplo = "Cuales es el peso de Mercurio"

# Tokenizar el texto de ejemplo y convertirlo a IDs
inputs = tokenizer(texto_ejemplo, return_tensors="pt")
input_ids = inputs["input_ids"]
attention_mask = inputs["attention_mask"]

# Realizar la predicción con probabilidades
with torch.no_grad():
    outputs = model(input_ids, attention_mask=attention_mask)
    probabilities = torch.softmax(outputs.logits, dim=1)

# Obtener la etiqueta predicha
predicted_label_id = torch.argmax(outputs.logits, dim=1).item()
predicted_probability = probabilities[0][predicted_label_id].item()

print("Texto de ejemplo:", texto_ejemplo)
print("Etiqueta predicha:", label_dict[predicted_label_id])
print("Probabilidad de la etiqueta predicha:", predicted_probability)

In [ ]:
!python -m spacy download es_core_news_md -q
!pip install pyspellchecker -q

In [ ]:
import re
import spacy
import pandas as pd
import nltk
from nltk.corpus import stopwords
from spellchecker import SpellChecker
from transformers import BertForSequenceClassification, BertTokenizer
import torch

nltk.download('stopwords')
nlp = spacy.load("es_core_news_md")
stop_words = set(stopwords.words('spanish'))
spell = SpellChecker(language='es')

def minusculas(text):
    # Convertir a minúsculas
    text = text.lower()
    return text

def lematizar(texto):
    doc = nlp(texto)
    lemas = ' '.join([token.lemma_ for token in doc])
    return lemas

def signos_puntuacion(text):
    # Sustituir acentos por letras sin acentos
    text = re.sub(r'[áäâà]', 'a', text)
    text = re.sub(r'[éêèë]', 'e', text)
    text = re.sub(r'[íîìï]', 'i', text)
    text = re.sub(r'[óôòö]', 'o', text)
    text = re.sub(r'[úûùü]', 'u', text)
    # Eliminar signos de puntuación
    text = re.sub(r'[^\w\s]', '', text)
    return text

def remove_stop_words(text):
    words = text.split()
    filtered_text = []
    for word in words:
        if word.lower() not in stop_words:
            filtered_text.append(word)
    return ' '.join(filtered_text)

# Función para corregir el texto
def corregir_texto(texto):
    palabras = texto.split()
    #corregido = [spell.correction(palabra) for palabra in palabras]
    corregido = [spell.correction(palabra) if spell.correction(palabra) is not None else palabra for palabra in palabras]
    texto_corregido = ' '.join(corregido)
    return texto_corregido

# Texto de ejemplo para procesar y hacer una predicción
#texto_ejemplo = "como afecta la atmosfera de marte a las misiones espaciales"
#texto_ejemplo = "cuales son los nombres de las lunas de urano"
texto_ejemplo = "¿Cuáles son las formaciones geológicas más destacadas en la superficie de Mercurio?"

# Aplicar preprocesamiento al texto de ejemplo
texto_procesado = minusculas(texto_ejemplo)
texto_procesado = signos_puntuacion(texto_procesado)
texto_procesado = corregir_texto(texto_procesado)
texto_procesado = lematizar(texto_procesado)
texto_procesado = remove_stop_words(texto_procesado)


ruta_modelo = '/content/modelo-clasficacion-preguntas'

# Cargar el modelo y el tokenizer
model = BertForSequenceClassification.from_pretrained(ruta_modelo)
tokenizer = BertTokenizer.from_pretrained(ruta_modelo)

# Tokenizar el texto de ejemplo procesado y convertirlo a IDs
inputs = tokenizer(texto_procesado, return_tensors="pt", padding=True, truncation=True, max_length=128)
input_ids = inputs["input_ids"]
attention_mask = inputs["attention_mask"]

# Realizar la predicción con probabilidades
with torch.no_grad():
    outputs = model(input_ids, attention_mask=attention_mask)
    probabilities = torch.softmax(outputs.logits, dim=1)

# Obtener la etiqueta predicha
predicted_label_id = torch.argmax(outputs.logits, dim=1).item()
predicted_probability = probabilities[0][predicted_label_id].item()

print("Texto de ejemplo original:", texto_ejemplo)
print("Texto de ejemplo procesado:", texto_procesado)
print("Etiqueta predicha:", label_dict[predicted_label_id])
print("Probabilidad de la etiqueta predicha:", predicted_probability)


In [ ]:
# Realizar la predicción con probabilidades
with torch.no_grad():
    outputs = model(input_ids, attention_mask=attention_mask)
    probabilities = torch.softmax(outputs.logits, dim=1)

# Obtener la etiqueta predicha
predicted_label_id = torch.argmax(outputs.logits, dim=1).item()
predicted_probability = probabilities[0][predicted_label_id].item()

# Obtener todas las probabilidades para las etiquetas predichas
#all_probabilities = probabilities[0].tolist()

print("Texto de ejemplo original:", texto_ejemplo)
print("Texto de ejemplo procesado:", texto_procesado)
print("Etiqueta predicha:", label_dict[predicted_label_id])
print("Probabilidad de la etiqueta predicha:", predicted_probability)

# Imprimir todas las probabilidades para todas las etiquetas
#print("Todas las probabilidades:", all_probabilities)
# Imprimir todas las probabilidades por separado
#for prob in all_probabilities:
#    print("Valor en la lista:", prob)
# Obtener todas las probabilidades para las etiquetas predichas con sus índices
all_probabilities = probabilities[0].tolist()
# Obtener índices ordenados por probabilidades en orden descendente
sorted_indexes = sorted(range(len(all_probabilities)), key=lambda k: all_probabilities[k], reverse=True)
# Imprimir las 10 probabilidades más altas y sus índices correspondientes
top_n = 10  # Obtener las 10 probabilidades más altas
for i, idx in enumerate(sorted_indexes[:top_n], 1):
    print(f"{i}. Valor en la lista: {all_probabilities[idx]}, Índice de etiqueta: {idx}, Etiqueta: {label_dict[idx]}")


In [ ]:
# Obtener la probabilidad más alta
max_probability = max(all_probabilities)
# Calcular y mostrar las 10 probabilidades más altas y sus porcentajes con respecto a la más alta
top_n = 10  # Obtener las 10 probabilidades más altas
for i, idx in enumerate(sorted_indexes[:top_n], 1):
    probability = all_probabilities[idx]
    percentage = (probability / max_probability) * 100 if max_probability > 0 else 0
    print(f"{i}. Valor en la lista: {probability}, Porcentaje con respecto al máximo: {percentage:.2f}%, Índice de etiqueta: {idx}, Etiqueta: {label_dict[idx]}")

In [ ]:
import random

# Suponiendo que 'predicted_label_id' contiene la etiqueta predicha

# Filtrar el DataFrame para obtener las filas con la etiqueta predicha
filas_etiqueta_predicha = df[df['label_codigo'] == predicted_label_id]

# Seleccionar aleatoriamente una fila
fila_aleatoria = filas_etiqueta_predicha.sample(n=1)

# Obtener el valor de la columna 'respuesta' de la fila seleccionada
respuesta_aleatoria = fila_aleatoria['respuesta'].values[0]

print("Respuesta aleatoria correspondiente a la etiqueta predicha:")
print(respuesta_aleatoria)
